In [8]:
! pip install tensorflow

    100% |████████████████████████████████| 92.6MB 40kB/s  eta 0:00:01  7% |██▎                             | 6.5MB 12.5MB/s eta 0:00:07��██████           | 61.0MB 37.1MB/s eta 0:00:01 | 65.4MB 73.3MB/s eta 0:00:01�███▏        | 67.0MB 68.6MB/s eta 0:00:01:01MB/s eta 0:00:02�███████████▉    | 80.4MB 60.1MB/s eta 0:00:010:00:0447.8MB/s eta 0:00:01��███████████████▊ | 88.9MB 67.6MB/s eta 0:00:01
    100% |████████████████████████████████| 1.2MB 1.1MB/s eta 0:00:01█▏           | 757kB 15.4MB/s eta 0:00:01��███████████████████████   | 1.1MB 18.2MB/s eta 0:00:01
    100% |████████████████████████████████| 61kB 26.1MB/s ta 0:00:01
    100% |████████████████████████████████| 368kB 4.4MB/s eta 0:00:01
    100% |████████████████████████████████| 3.2MB 392kB/s eta 0:00:01��██████████████▉   | 2.9MB 50.3MB/s eta 0:00:01��███████████████████████████▉| 3.2MB 41.8MB/s eta 0:00:01
    100% |████████████████████████████████| 61kB 26.3MB/s ta 0:00:01
    100% |████████████████████████████████| 10.8MB 2

In [9]:
from __future__ import absolute_import
from __future__ import print_function

import time
import os
import numpy as np
import scipy.integrate
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
#import plotly.plotly as py
import plotly.graph_objs as go
import plotly.io as pio

import tensorflow as tf
print("tensorflow version: ", tf.__version__)

tensorflow version:  1.13.1


In [10]:
tf.enable_eager_execution()
init_notebook_mode(connected=True)

In [11]:
config = tf.ConfigProto()
config.gpu_options.allow_growth=True

os.environ['CUDA_VISIBLE_DEVICES'] = '0'

In [12]:
ts = np.linspace(0., 4.0, 10)

ys, info = tf.contrib.integrate.odeint(lambda y, t: tf.to_float(2*t), 0.0, ts, rtol = 0.01, full_output=True)

iplot([go.Scatter(x=ts, y=ys.numpy())])


For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
If you depend on functionality not listed there, please file an issue.

Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.


In [13]:
ts = np.linspace(0., 4.0, 10)

ys = scipy.integrate.odeint(lambda y, t: 2*t, [0.0], ts)

iplot([go.Scatter(x=ts, y=np.squeeze(ys))])

In [14]:
# z = [x, y]
def damped_oscillator_2d(z, t, A):
    return np.dot(z**3, A)

A = np.array([
    # −0.1x^3 + 2.0y^3
    [-0.1, 2.0],
    # −2.0x^3 − 0.1y^3
    [-2.0, -0.1]])

# Initial u0 = [x0, y0]
z0 = np.array([2., 0.]).T

# Time sampling
N = 1000  # Dataset size
max_T = 25.0 # Time sampling
ts = np.linspace(0., max_T, N)

In [15]:
zs, info = tf.contrib.integrate.odeint(lambda z0, ts: tf.tensordot(z0**3, A, axes=1), z0, ts,
                                method="dopri5", options={"max_num_steps":10, "first_step": 0.1}, rtol = 0.001,
                                full_output=True)
zs = zs.numpy()
xs = zs[:, 0]
ys = zs[:, 1]
iplot([go.Scatter(x=ts, y=xs, name="x"), go.Scatter(x=ts, y=ys, name="y")])
iplot([go.Scatter(x=xs, y=ys)])

In [16]:
zs = scipy.integrate.odeint(damped_oscillator_2d, z0, ts, args=(A,))

xs = zs[:, 0]
ys = zs[:, 1]
iplot([go.Scatter(x=ts, y=xs, name="x"), go.Scatter(x=ts, y=ys, name="y")])
iplot([go.Scatter(x=xs, y=ys)])

In [17]:
def ode_tf(f, z0, ts, args):
    """calls Full TF ODE Runge-Kutta Dopri5 Solver
    
    Args:
        f: a function of type (z0, ts, args) -> ys
            where z0, the initial value
                  ts, the time values
                  args, the supplementary args

        z0: initial value
        ts: time values on which to solve equation
        args: supplementary arsg
        
    Returns:
        array of solutions computed by ODE Solver
    Please note, TF solver params are hard-coded here but they could be managed in a cleaner way
    """
    # current TF odeint implementation doesn't manage args so we need this lambda
    zs, info = tf.contrib.integrate.odeint(
        lambda z0, ts: f(z0, ts, args), z0, ts,
        method="dopri5",
        options={"max_num_steps":1000, "first_step": 0.001},
        rtol = 0.001,
        full_output=True
    )
    return zs

def ode_tf_batch(f, z0s, ts, args):
    """Calls Full TF ODE Runge-Kutta Dopri5 Solver simulating Batch Mode by splitting on batch dim
    to compare to using ode_tf in batch mode (batch management is not what you expect)
    """
    rs = []
    for z0 in tf.split(z0s, z0s.shape[0], axis=0):
        z0 = tf.squeeze(z0)
        r = ode_tf(f, z0, ts, args)
        r = tf.expand_dims(r, axis=0)
        rs.append(r)
    rs = tf.keras.backend.concatenate(rs, axis=0)
    return rs

def ode_scipy(f, z0, ts, args):
    """Calls Python Scipy ODE Solver from TF
    
    Args:
        f: a function of type (z0, ts, args) -> ys
            where z0, the initial value
                  ts, the time values
                  args, the supplementary args

        y-z0: initial value
        ts: time values on which to solve equation
        args: supplementary args

    Returns:
        array of solutions computed by ODE Solver
    """
    # managing args as None... this is ugly but simplifies a bit later code
    if args is not None:
        r = tf.py_func(
            lambda z0, ts, args: scipy.integrate.odeint(f, z0, ts, args=(args,)),
            [z0, ts, args], z0.dtype)
    else:
        r = tf.py_func(
            lambda z0, ts: scipy.integrate.odeint(f, z0, ts, args=(None,)),
            [z0, ts], z0.dtype)
    return r


def ode_scipy_batch(f, z0s, ts, args):
    """Calls Python Scipy Solver simulating Batch Mode by splitting along batch dim"""
    rs = []
    for z0 in tf.split(z0s, z0s.shape[0], axis=0):
        z0 = tf.squeeze(z0)
        r = ode_scipy(f, z0, ts, args)
        r = tf.expand_dims(r, axis=0)
        rs.append(r)
    rs = tf.keras.backend.concatenate(rs, axis=0)
    return rs

In [18]:
# Numpy or eager-mode TF
def lotka_volterra(z, ts, args):
    # batch mode on z
    if len(z.shape) > 1:
        x, y = z[:, 0], z[:, 1]
        α, β, δ, γ = args[0], args[1], args[2], args[3]
        dx = α*x - β*x*y
        dy = -δ*y + γ*x*y
        return tf.stack([dx, dy], axis=1)
    else:
        x, y = z[0], z[1]
        α, β, δ, γ = args[0], args[1], args[2], args[3]
        dx = α*x - β*x*y
        dy = -δ*y + γ*x*y
        return tf.stack([dx, dy], axis=0)

# Tensorflow Variables
D = 2
# time interval from 0 to 10 divided in 100 steps
N = 1000
ts = tf.constant(np.linspace(0., 10.0, N))
# initial arguments
args = tf.Variable(tf.constant([1.5, 1.0, 3.0, 1.0], shape=(4,), dtype=ts.dtype))
z0 = tf.Variable(tf.constant([1.0,1.0], shape=(2,), dtype=ts.dtype))

In [19]:
sol = ode_tf(lotka_volterra, z0, ts, args)
xs = sol[:, 0].numpy()
ys = sol[:, 1].numpy()

iplot([go.Scatter(x=ts.numpy(), y=xs, name="x"), go.Scatter(x=ts.numpy(), y=ys, name="y")])

iplot([go.Scatter(x=xs, y=ys)])

Instructions for updating:
Colocations handled automatically by placer.


In [20]:
sol = ode_scipy(lotka_volterra, z0, ts, args)
xs = sol[:, 0].numpy()
ys = sol[:, 1].numpy()

iplot([go.Scatter(x=ts.numpy(), y=xs, name="x"), go.Scatter(x=ts.numpy(), y=ys, name="y")])

iplot([go.Scatter(x=xs, y=ys)])

Instructions for updating:
tf.py_func is deprecated in TF V2. Instead, use
    tf.py_function, which takes a python function which manipulates tf eager
    tensors instead of numpy arrays. It's easy to convert a tf eager tensor to
    an ndarray (just call tensor.numpy()) but having access to eager tensors
    means `tf.py_function`s can use accelerators such as GPUs as well as
    being differentiable using a gradient tape.
    


In [21]:
z1 = tf.expand_dims(z0, -1)
z0s = tf.tile(tf.expand_dims(z0, -1), [1, 2])
sol = ode_scipy_batch(lotka_volterra, z0s, ts, args)
print(sol.shape)

(2, 1000, 2)


In [22]:
def flatten(params):
    """flatten a list of tensors/arrays into a flat tensor and returns also the unflatten function
    able to rebuild original list from flattenned tensor
    """
    if len(params) == 0:
        def unflatten(flat_params):
            return flat_params
        return np.array(params), unflatten
    
    original_shapes = []
    flat_params = []
    default_dtype = params[0].dtype
    for p in params:
        sh = p.shape
        original_shapes.append(sh)
        flat_sh = 1
        for s in sh:
            flat_sh *= s

        res = tf.reshape(p, (flat_sh,))
        res = tf.cast(res, default_dtype)
        flat_params.append(res)
    
    def unflatten(flat_params):
        cur_idx = 0
        params = []
        for sh in original_shapes:
            flat_sh = 1
            for s in sh:
                flat_sh *= s
            param = flat_params[cur_idx:cur_idx + flat_sh]
            param = tf.reshape(param, sh)
            cur_idx += int(flat_sh)
            params.append(param)
            
        return params
            
    flat_params = tf.concat(flat_params, axis=0)
    return flat_params, unflatten

# Directly inspired from function implemented with autograd at the end of the paper
# Extended from "Scalable Inference of Ordinary Differential
# Equation Models of Biochemical Processes", Sec. 2.4.2
# Fabian Froehlich, Carolin Loos, Jan Hasenauer, 2017
# https://arxiv.org/abs/1711.08079
def grad_odeint(z_ts, func, ts, args, T, D, ode_solver, variables = None):
    """
    This code is still ugly and not very robust IMHO...
    It's full of reshape that might be unneeded but at least I know what I manipulate without compilted types
    
    Args:
        z_ts: the values with ODE Solver in forward path on ts time values
        func: the adjoint gradient function to integrate with ODE Solver
        ts: the discretized time values
        args: the derivable arguments of func
        ode_solver: the ode_solver function (z0, ts, args) -> zs
        variables: the hidden TF/Keras tensor variables (separated from args to be manageable as they have their own life cycle I'm not sure to understand yet)

    Returns:
        grad: the custom augmentate-state TF gradient function
    """
    # let's store
    if variables is not None:
        flat_variables, unflatten_variables = flatten(variables)

    def unpack_D_2D(x, D):
        """simple extract """
        x = tf.squeeze(x)
        return (
            x[0:D],
            x[D:2 * D]
        )
        
    # augmented_state = [z_t, a_z_t, a_t, a_args, a_vars]
    def a_gradient_aug(augmented_state, t, args):
        augmented_state = tf.convert_to_tensor(augmented_state, dtype=z_ts.dtype)
        t = tf.convert_to_tensor(t, dtype=ts.dtype)
        t = tf.reshape(t, (1,))
        args = tf.convert_to_tensor(args, dtype=args.dtype)
        z_t, a_z_t = unpack_D_2D(augmented_state, z_ts.shape[1])

        # the internal gradient-tape computing second derivative
        with tf.GradientTape() as gg:
            gg.watch(args)                
            gg.watch(a_z_t)
            gg.watch(t)
            gg.watch(z_t)
            dz_dt = func(z_t, t, args)

        if variables is not None:
            da_z_dt, da_t_dt, da_args_dargs, da_dvars = gg.gradient(
                dz_dt, [z_t, t, args, variables], output_gradients = -a_z_t)
        else:
            da_z_dt, da_t_dt, da_args_dargs = gg.gradient(
                dz_dt, [z_t, t, args], output_gradients = -a_z_t)
            da_dvars = None
        
        if da_z_dt is None:
            da_z_dt = tf.zeros_like(z_t, dtype=z_t.dtype)
        if da_t_dt is None:
            da_t_dt = tf.zeros_like(t, dtype=t.dtype)
        if da_args_dargs is None:
            da_args_dargs = tf.zeros_like(args, dtype=args.dtype)
        if da_dvars is None:
            da_dvars = tf.zeros_like((1,))
        else:
            da_dvars, _ = flatten(da_dvars)
        r, _ = flatten([dz_dt, da_z_dt, da_t_dt, da_args_dargs, da_dvars])
        return r

    def grad(gt):
        """the TF custom gradient function"""
        
        # initialization of backward gradient computation starting at the end of time interval
        dl_dz_t = gt[-1, :]
        dl_dt0 = tf.constant([0.], shape=(1,), dtype=ts.dtype)
        dl_dargs = tf.zeros_like(args, dtype=ts.dtype)
        if variables is not None:
            dl_dvars = tf.zeros_like(flat_variables, dtype=flat_variables.dtype)
        else:
            dl_dvars = tf.zeros((1,))
        dl_dt_list = []

        # compute gradient back-propagation by ODE solver calls going backward in time
        for i in range(T - 1, 0, -1):
            # Compute effect of moving back in time (just porting formulas found in paper)
            ztsi = z_ts[i, :]
            gti = gt[i, :]
            # Compute the adjoint gradient of loss at current time
            fi = func(ztsi, ts[i], args)
            dl_dt = tf.tensordot(fi, tf.transpose(gti), axes=1) #, axes=[[1], [0]])
            #dl_dt = tf.reshape(dl_dt, (1,))
            dl_dt_list.append(dl_dt)
            dl_dt0 = dl_dt0 - dl_dt
            #dl_dt0 = tf.reshape(dl_dt0, shape=(1,))
            # build augmented state
            aug_z0, unflatten_aug = flatten([ztsi, dl_dz_t, dl_dt0, dl_dargs, dl_dvars])
            # Run augmented system backwards to the previous observation using ODE_Solver
            cur_ts = tf.reverse(tf.slice(ts, [i-1], [2]), axis=[0])
            a_aug = ode_solver(lambda aug, t, args: a_gradient_aug(aug, t, args), aug_z0, cur_ts, args)

            # get at ts[i - 1]
            a_aug = a_aug[1]
            _, dl_dz_t, dl_dt0, dl_dargs, dl_dvars = unflatten_aug(a_aug)

            # Add gradient from current output.
            dl_dz_t = dl_dz_t + gt[i - 1, :]

        #dl_dt0 = tf.reshape(dl_dt0, (1,))
        dl_dt_list.append(dl_dt0)
        dl_dts = tf.stack(dl_dt_list, axis=0)
        dl_dts = tf.reverse(dl_dts, axis=[0])

        # output z_t is not needed but can't put None in TF tensors
        n_o_n_e = tf.zeros_like(z_ts) #, dtype=z_ts.dtype)
        
        if variables is not None:
            return [n_o_n_e, dl_dz_t, dl_dts, dl_dargs], unflatten_variables(dl_dvars)
        else:
            return [n_o_n_e, dl_dz_t, dl_dts, dl_dargs], []
    return grad

def tf_ode_grad(f, N, D, ode_solver):
    """The plug in custom_gradient TF mechanism"""
    @tf.custom_gradient
    def custom_grad(z0, ts, args):
        z0 = tf.squeeze(z0)
        # forward values computation with ODE Solver
        ys = ode_solver(f, z0, ts, args)
        def grad_fn(dr, variables=None):
            # backward gradient computation using backward ODE Solver
            (_, dl_dz_t, dl_dts, dl_dargs), dl_dvars = grad_odeint(ys, f, ts, args, N, D, ode_solver, variables)(dr)
            return [dl_dz_t, dl_dts, dl_dargs], dl_dvars
        return ys, grad_fn
    return custom_grad

In [23]:
def flatten_batch(params):
    """Batch-aware flatten a list of tensors/arrays into a flat tensor and returns also the unflatten function
    able to rebuild original list from flattenned tensor
    """
    if len(params) == 0:
        def unflatten(flat_params):
            return flat_params
        return np.array(params), unflatten
    
    original_shapes = []
    flat_params = []
    default_dtype = params[0].dtype
    batch_size = params[0].shape[0]
    for p in params:
        sh = p.shape
        original_shapes.append(sh)
        flat_sh = 1
        for s in sh[1:]:
            flat_sh *= s

        res = tf.reshape(p, (batch_size, flat_sh,))
        res = tf.cast(res, default_dtype)
        flat_params.append(res)
    
    def unflatten(flat_params):
        cur_idx = 0
        params = []
        for sh in original_shapes:
            flat_sh = 1
            for s in sh[1:]:
                flat_sh *= s
            param = flat_params[:, cur_idx:cur_idx+flat_sh]
            param = tf.reshape(param, sh)
            cur_idx += int(flat_sh)
            params.append(param)
            
        return params
            
    flat_params = tf.concat(flat_params, axis=1)
    return flat_params, unflatten
    
    

# Directly inspired from function implemented with autograd at the end of the paper
# Extended from "Scalable Inference of Ordinary Differential
# Equation Models of Biochemical Processes", Sec. 2.4.2
# Fabian Froehlich, Carolin Loos, Jan Hasenauer, 2017
# https://arxiv.org/abs/1711.08079
def grad_odeint_batch(z_ts, func, ts, args, T, D, ode_solver, variables = None):
    """
    Batch-aware augmented gradient
    
    Args:
        z_ts: (batch_size, batch_time, D) the values with ODE Solver in forward path on ts time values
        func: the adjoint gradient function to integrate with ODE Solver
        ts: (batch_time,) the discretized time values
        args: the derivable arguments of func
        ode_solver: the ode_solver function (z0, ts, args) -> zs
        variables: the hidden TF/Keras tensor variables (separated from args to be manageable as they have their own life cycle I'm not sure to understand yet)

    Returns:
        grad: the custom augmentate-state TF gradient function
    """
    # let's store
    if variables is not None:
        flat_variables, unflatten_variables = flatten(variables)
        vars_batch = []
        for var in variables:            
            var = tf.expand_dims(var, 0)
            if len(var.shape) > 2:
                var = tf.tile(var, [z_ts.shape[0], 1, 1])
            else:
                var = tf.tile(var, [z_ts.shape[0], 1])
            
            vars_batch.append(var)
        flat_variables_batch, unflatten_variables_batch = flatten_batch(vars_batch)
        

    def unpack_D_2D(x, D):
        """simple extract """
        #x = tf.squeeze(x)
        if len(x.shape) > 1:
            return (
                x[:, 0:D],
                x[:, D:2 * D]
            )
        else:
            return (
                x[0:D],
                x[D:2 * D]
            )
        
    # batch-aware gradient function able to manage (could replace simpler impl in next version)
    # augmented_state = [z_t, a_z_t, a_t, a_args, a_vars]
    def a_gradient_aug(augmented_state, t, args):
        augmented_state = tf.convert_to_tensor(augmented_state, dtype=z_ts.dtype)
        t = tf.convert_to_tensor(t, dtype=ts.dtype)
        #t = tf.reshape(t, (1,))
        args = tf.convert_to_tensor(args, dtype=args.dtype)
        z_t, a_z_t = unpack_D_2D(augmented_state, D)

        # the internal gradient-tape computing second derivative
        with tf.GradientTape() as gg:
            gg.watch(args)                
            gg.watch(a_z_t)
            gg.watch(t)
            gg.watch(z_t)
            dz_dt = func(z_t, t, args)
            dz_dt = tf.cast(dz_dt, z_t.dtype)
        if variables is not None:
            da_z_dt, da_t_dt, da_args_dargs, da_dvars = gg.gradient(
                dz_dt, [z_t, t, args, variables], output_gradients = -a_z_t)
        else:
            da_z_dt, da_t_dt, da_args_dargs = gg.gradient(
                dz_dt, [z_t, t, args], output_gradients = -a_z_t)
            da_dvars = None
        
        if len(augmented_state.shape) > 1:
            if da_z_dt is None:
                da_z_dt = tf.zeros_like(z_t, dtype=z_t.dtype)
            if da_t_dt is None:
                da_t_dt = tf.zeros((z_ts.shape[0],), dtype=t.dtype)

            if da_args_dargs is None:
                da_args_dargs = tf.zeros_like(args, dtype=ts.dtype)
            da_args_dargs = tf.expand_dims(da_args_dargs, 0)
            da_args_dargs = tf.tile(da_args_dargs, [z_ts.shape[0], 1])

            if da_dvars is None:
                da_dvars = tf.zeros((z_ts.shape[0],))
            else:
                da_dvars, _ = flatten(da_dvars)
            da_dvars = tf.expand_dims(da_dvars, 0)
            da_dvars = tf.tile(da_dvars, [z_ts.shape[0], 1])

            r, _ = flatten_batch([dz_dt, da_z_dt, da_t_dt, da_args_dargs, da_dvars])
        else:
            if da_z_dt is None:
                da_z_dt = tf.zeros_like(z_t, dtype=z_t.dtype)
            if da_t_dt is None:
                da_t_dt = tf.zeros_like(t, dtype=t.dtype)

            if da_args_dargs is None:
                da_args_dargs = tf.zeros_like(args, dtype=args.dtype)

            if da_dvars is None:
                da_dvars = tf.zeros((1,))
            else:
                da_dvars, _ = flatten(da_dvars)
            r, _ = flatten([dz_dt, da_z_dt, da_t_dt, da_args_dargs, da_dvars])
        return r

    def grad(gt): # (batch_size, batch_time, D)
        """the TF custom gradient function"""
        
        # initialization of backward gradient computation starting at the end of time interval
        dl_dz_t = gt[:, -1, :] # (batch_size, D)
        dl_dt0 = tf.zeros((z_ts.shape[0],), dtype=ts.dtype)
        # init args gradient
        if args is not None:
            dl_dargs = tf.expand_dims(tf.zeros_like(args, dtype=ts.dtype), 0)
            dl_dargs = tf.tile(dl_dargs, [z_ts.shape[0], 1])
        
        # init variables gradient
        if variables is not None:
            dl_dvars = tf.zeros_like(flat_variables, dtype=flat_variables.dtype)
        else:
            dl_dvars = tf.zeros((z_ts.shape[0],))
        dl_dvars = tf.expand_dims(dl_dvars, 0)
        dl_dvars = tf.tile(dl_dvars, [z_ts.shape[0], 1])
        
        dl_dt_list = []

        # compute gradient back-propagation by ODE solver calls going backward in time
        for i in range(T - 1, 0, -1):
            # Compute effect of moving back in time (just porting formulas found in paper)
            ztsi = z_ts[:, i, :] # (batch_size, D)
            gti = gt[:, i, :] # (batch_size, D)
            gti = tf.expand_dims(gti, 1) # (batch_size, 1, D)
            # Compute the adjoint gradient of loss at current time
            fi = func(ztsi, ts[i], args) # (batch_size, D)
            fi = tf.expand_dims(fi, 1) # (batch_size, 1, D)
            fi = tf.cast(fi, ztsi.dtype)
            dl_dt = tf.einsum("ijk,ikj->i", fi, gti) # (batch_size, 1)
            dl_dt_list.append(dl_dt)
            dl_dt0 = dl_dt0 - dl_dt
            # build augmented state
            aug_z0, unflatten_aug = flatten_batch([ztsi, dl_dz_t, dl_dt0, dl_dargs, dl_dvars])
            # Run augmented system backwards to the previous observation using ODE_Solver
            cur_ts = tf.reverse(tf.slice(ts, [i-1], [2]), axis=[0])
            a_aug = ode_solver(lambda aug, t, args: a_gradient_aug(aug, t, args), aug_z0, cur_ts, args)

            # get at ts[i - 1]
            a_aug = a_aug[:, 1]
            _, dl_dz_t, dl_dt0, dl_dargs, dl_dvars = unflatten_aug(a_aug)

            # Add gradient from current output.
            dl_dz_t = dl_dz_t + gt[:, i - 1, :]

        #dl_dt0 = tf.reshape(dl_dt0, (1,))
        dl_dt_list.append(dl_dt0)
        dl_dts = tf.stack(dl_dt_list, axis=1)
        dl_dts = tf.reverse(dl_dts, axis=[1])

        # output z_t is not needed but can't put None in TF tensors
        n_o_n_e = tf.zeros_like(z_ts) #, dtype=z_ts.dtype)

        if variables is not None:
            return [n_o_n_e, dl_dz_t, dl_dts, dl_dargs], unflatten_variables_batch(dl_dvars)
        else:
            return [n_o_n_e, dl_dz_t, dl_dts, dl_dargs], []
    return grad


def tf_ode_grad_batch(f, N, D, ode_solver):
    """The plug in custom_gradient TF mechanism"""
    @tf.custom_gradient
    def custom_grad(z0, ts, args):
        z0 = tf.squeeze(z0)
        # forward values computation with ODE Solver
        ys = ode_solver(f, z0, ts, args)
        def grad_fn(dr, variables=None):
            # backward gradient computation using backward ODE Solver
            (_, dl_dz_t, dl_dts, dl_dargs), dl_dvars = grad_odeint_batch(ys, f, ts, args, N, D, ode_solver, variables)(dr)
            return [dl_dz_t, dl_dts, dl_dargs], dl_dvars
        return ys, grad_fn
    return custom_grad

In [24]:
def loss_L2(y_true, y_pred):
    """The classic derivable least-square loss function"""
    return tf.reduce_mean(tf.square(y_true - y_pred))

def loss_L1(y_true, y_pred):
    """The classic derivable least-square loss function"""
    return tf.reduce_mean(tf.abs(y_true - y_pred))

In [25]:
from IPython import display

def optimize_batch(f, ode_solver, loss_fn, labels, z0, ts,
             args=None, variables=None,
             epochs=25, test_freq=10,
             batch_time=10, data_size=50, batch_size=10,
             x_axis_min=-0.25, x_axis_max=10.25,
             y_axis_min=-0.25, y_axis_max=7.0,
             x2_axis_min=-0.25, x2_axis_max=10.25,
             y2_axis_min=-0.25, y2_axis_max=7.0,
             learning_rate=0.1, epsilon=1e-7, output_dir="images", start = 0):
    """Random Mini-batch optimization process on args/variables parameters of a function
    defined by its derivative f integrated with ODE Solver according to a loss function loss_fn,
    groundtruth labels, initial input value and time interval sampling using Adam optimizer
    (with plots & image saving)"""

    def build_layout(
        x_axis_min, x_axis_max, y_axis_min, y_axis_max,
        x2_axis_min, x2_axis_max, y2_axis_min, y2_axis_max,
        height=680, width=1024
    ):
        # plotting layout
        layout = go.Layout(
            xaxis=dict(
                range=[x_axis_min, x_axis_max],
            ),
            yaxis=dict(
                range=[y_axis_min, y_axis_max],
                domain=[0.55, 1.0],
            ),
            xaxis2=dict(
                range=[x2_axis_min, x2_axis_max],
            ),
            yaxis2=dict(
                range=[y2_axis_min, y2_axis_max],
                domain=[0, 0.45],  
            ),
            title="",
            height=height, width=width
        )
        return layout

    def build_figure(ts, labels, loss, best_zss, best_loss, global_step, layout):
        data = []

        for zs in best_zss[-1:]:
            data.extend([
                go.Scatter(x=ts.numpy(), y=zs[:, 0], name="best_x",
                           mode = 'lines+markers',
                           line = dict(
                                color = ('rgb(34, 119, 158)'),
                                width = 1)),
                go.Scatter(x=ts.numpy(), y=zs[:, 1], name="best_y",
                           mode = 'lines+markers',
                           line = dict(
                                color = ('rgb(201, 79, 14)'),
                                width = 1)),
                go.Scatter(x=zs[:, 0], y=zs[:, 1], name="best_xy",
                           xaxis="x2", yaxis="y2",
                           mode = 'lines+markers',
                           line = dict(
                                color = ('rgb(8, 173, 99)'),
                                width = 1)),
            ])

        data.extend([            
            go.Scatter(x=ts.numpy(), y=labels.numpy()[:, 0], name="groundtruth_x",
                       line = dict(
                            color = ('rgb(34, 119, 158)'),
                            width = 2,
                            dash = 'dot')),
            go.Scatter(x=ts.numpy(), y=labels.numpy()[:, 1], name="groundtruth_y",
                       line = dict(
                            color = ('rgb(201, 79, 14)'),
                            width = 2,
                            dash = 'dot')),
            go.Scatter(x=labels.numpy()[:, 0], y=labels.numpy()[:, 1], name="groundtruth_xy",
                       xaxis="x2", yaxis="y2",
                       line = dict(
                            color = ('rgb(173, 7, 7)'),
                            width = 2,
                            dash = 'dot')),
        ])
        if loss >= best_loss:
            data.extend([                
                go.Scatter(x=ts.numpy(), y=last_ys[:, 0], name="current_x",
                           line = dict(
                                    color = ('rgb(24, 24, 24)'),
                                    width = 1,
                                    dash = 'dash')),
                go.Scatter(x=ts.numpy(), y=last_ys[:, 1], name="current_y",
                           line = dict(
                                    color = ('rgb(24, 24, 24)'),
                                    width = 1,
                                    dash = 'dash')),
                go.Scatter(x=last_ys[:, 0], y=last_ys[:, 1], name="current_xy",
                           xaxis="x2", yaxis="y2",
                           line = dict(
                                color = ('rgb(24, 24, 24)'),
                                width = 2,
                                dash = 'dash')),
            ])

        layout.title = f"Step {global_step.numpy()}<br>Best Loss {best_loss.numpy()}<br>Current Loss {loss.numpy()}"
        fig = go.Figure(data=data, layout=layout)

        return layout, fig


    def custom_grad(z0, ts, batch_labels, the_args):
        with tf.GradientTape() as tape:
            tape.watch(z0)
            tape.watch(the_args)
            ode = tf_ode_grad_batch(f, batch_time, D, ode_solver)(z0, ts, the_args)
            loss = loss_fn(batch_labels, ode)

        # managing stupidly the abscence of args or variables...
        if variables is not None:
            grads, grad_vars = tape.gradient(loss, [[the_args], variables])
        else:
            grads = tape.gradient(loss, [the_args])
            grad_vars = []

        the_grads = []
        for grad in grads:
            #grad = tf.reshape(grad, the_args.shape)
            grad = tf.cast(grad, the_args.dtype)
            the_grads.append(grad)
            
        the_grad_vars = []
        for i, grad in enumerate(grad_vars):
            the_grad_vars.append(tf.cast(grad, variables[i].dtype))
            
        return loss, ode, the_grads, the_grad_vars

    # Adam Optimizer
    optimizer = tf.train.AdamOptimizer(learning_rate=learning_rate,
                                       epsilon=epsilon)

    def get_batch():
        #s = torch.from_numpy(np.random.choice(np.arange(data_size - batch_time, dtype=np.int64), batch_size, replace=False))
        start_indices = np.random.choice(np.arange(data_size - batch_time, dtype=np.int64), batch_size, replace=False)
        batch_z0 = []
        for idx in start_indices:
            batch_z0.append(labels[idx])

        batch_ts = ts[:batch_time]  # (T)
        batch_zs = []
        for i, s in enumerate(start_indices):
            batch_zs.append(labels[s:s+batch_time, :])
        batch_zs = tf.stack(batch_zs, axis=0)
        return batch_z0, batch_ts, batch_zs
    
    layout = build_layout(
        x_axis_min, x_axis_max, y_axis_min, y_axis_max,
        x2_axis_min, x2_axis_max, y2_axis_min, y2_axis_max)
    
    # no args, replacing it by a fake tf.Variable for now... to be removed later
    if args is None:
        var_args = tf.Variable([0], dtype=tf.float64)
    else:
        var_args = args
    
    # the training loop
    global_step = tf.Variable(start)
    best_loss = 1e400
    best_zss = []

    if not os.path.exists(output_dir):
        os.mkdir(output_dir)
    
    for epoch in range(epochs):
        batch_z0, batch_ts, batch_labels = get_batch()
        
        loss, ode, grads, grad_vars = custom_grad(batch_z0, batch_ts, batch_labels, var_args)
        print("batch_loss:", loss)

        accum_grads = [tf.reduce_mean(grad, axis=0) for grad in grads]
        grad_params = list(zip(accum_grads, [var_args]))
        if variables is not None:
            accum_grad_vars = [tf.reduce_mean(grad, axis=0) for grad in grad_vars]
            grad_params.extend(list(zip(accum_grad_vars, variables)))
                    
        optimizer.apply_gradients(grad_params, global_step)
        
        ode = tf_ode_grad(f, N, D, ode_solver)(z0, ts, var_args)
        loss = loss_fn(labels, ode)
        ys = ode.numpy()
        last_ts = ts.numpy()
        last_ys = ys
        
        if loss < best_loss:
            best_loss = loss
            best_var_args = var_args
            #best_ts = ts.numpy()
            best_zs = ys
            best_zss.append(best_zs)

        # More Plotting
        if global_step.numpy() % test_freq == 0:
            display.clear_output(wait=True)        
            layout, fig = build_figure(ts, labels, loss, best_zss, best_loss, global_step, layout)
            iplot(fig)
            pio.write_image(fig, f"{output_dir}/step_{global_step.numpy()}.png")

        #print(f"Step: {global_step.numpy()}, Loss: {loss.numpy()}")

In [26]:
# Tensorflow Variables
# the dimension of our input vector [x, y] => 2
D = 2
# time interval sampling
N = 1000
batch_time=10
batch_size=5
ts = tf.constant(np.linspace(0., 10.0, N))
# the arguments we want to optimize
args = tf.Variable(tf.constant([1.5, 1.0, 3.0, 1.0], shape=(4,), dtype=ts.dtype))
z0 = tf.Variable(tf.constant([1.0,1.0], shape=(2,), dtype=ts.dtype))

def ode_scipy_solver(f, z0, ts, args):
    r = ode_scipy(f, z0, ts, args)
    r = tf.cast(r, z0.dtype)
    return r

def ode_scipy_batch_solver(f, z0s, ts, args):
    if len(z0s.shape) > 1:
        r = ode_scipy_batch(f, z0s, ts, args)
        r = tf.cast(r, z0s.dtype)
        return r
    else:
        return ode_scipy_solver(f, z0s, ts, args)

ground_truth_ones = tf.ones(shape=(N, D), dtype=z0.dtype)

In [27]:
optimize_batch(lotka_volterra, ode_scipy_batch_solver, loss_L2,
         ground_truth_ones, z0, ts,
         args=args, variables=None,
         epochs=25, test_freq=1,
         batch_time=batch_time, data_size=N, batch_size=batch_size,
         y_axis_min=-0.25, y_axis_max=7.0,
         x_axis_min=-0.25, x_axis_max=10.25,
         output_dir="lotka_volterra_optim_scipy")

RuntimeError: The size of the array returned by func (10) does not match the size of y0 (14).

In [39]:
! pip install psutil

In [40]:
# Tensorflow Variables
# the dimension of our input vector [x, y] => 2
D = 2
N = 200
batch_time=50
batch_size=4
ts = tf.constant(np.linspace(0., 10.0, N))
# the arguments we want to optimize
args = tf.Variable(tf.constant([1.5, 1.0, 3.0, 1.0], shape=(4,), dtype=ts.dtype))

# the initial input value
z0 = tf.Variable(tf.constant([1.0,1.0], shape=(2,), dtype=ts.dtype))

def ode_tf_solver(f, z0, ts, args):
    # f is considered time-invariant for now so who cares about order
    # order is required by TF odeint
    ts = tf.contrib.framework.sort(ts)
    r = ode_tf(f, z0, ts, args)
    r = tf.cast(r, z0.dtype)
    return r

def ode_tf_batch_solver(f, z0s, ts, args):
    if len(z0s.shape) > 1:
        r = ode_tf_solver(f, z0s, ts, args)
        r = tf.transpose(r, [1, 0, 2])
        #ts = tf.contrib.framework.sort(ts)
        #r = ode_tf_batch(f, z0s, ts, args)
        return r
    else:
        return ode_tf_solver(f, z0s, ts, args)

# our ground_truth (all 1.0)
ground_truth_ones = tf.ones(shape=(N, D), dtype=z0.dtype)

In [41]:
optimize_batch(lotka_volterra, ode_tf_batch_solver, loss_L2,
         ground_truth_ones, z0, ts,
         args=args, variables=None,
         epochs=25, test_freq=1,
         batch_time=batch_time, data_size=N, batch_size=batch_size,
         y_axis_min=-0.25, y_axis_max=7.0,
         x_axis_min=-0.25, x_axis_max=10.25,
         output_dir="lotka_volterra_optim_tf")

ValueError: Image generation requires the psutil package.

Install using pip:
    $ pip install psutil
    
Install using conda:
    $ conda install psutil


In [33]:
## D = 2
N = 1000
batch_time=10
batch_size=20
ts = tf.constant(np.linspace(0., 10.0, N))
args = tf.Variable(tf.constant([1.5, 1.0, 3.0, 1.0], shape=(4,), dtype=ts.dtype))
z0 = tf.Variable(tf.constant([1.0, 1.0], shape=(2,), dtype=ts.dtype))

model = tf.keras.Sequential([
  tf.keras.layers.Dense(25, activation=tf.nn.relu, input_shape=(1, D)),  # input shape required
  tf.keras.layers.Dense(D)
])

def predict_fn(y, ts, args):
    rank =  tf.rank(y).numpy()
    if rank == 1:
        y = tf.expand_dims(y, 0)
    y = tf.cast(y, tf.float32)
    r = model(y)
    if rank == 1:
        r = tf.squeeze(r)
    r = tf.cast(r, y.dtype)
    return r

ground_truth = ode_scipy(lotka_volterra, z0, ts, args)

In [34]:
optimize_batch(predict_fn, ode_scipy_batch_solver, loss_L2,
         ground_truth, z0, ts,
         args=None, variables=model.variables,
         epochs=500, test_freq=1, learning_rate=0.01,
         batch_time=batch_time, data_size=N, batch_size=batch_size,
         x_axis_min=-0.25, x_axis_max=10.25,
         y_axis_min=-0.25, y_axis_max=8.0,
         x2_axis_min=-0.25, x2_axis_max=8.0,
         y2_axis_min=-0.25, y2_axis_max=8.0,
         output_dir="ode_dense_lotka_volterra")

ValueError: Image generation requires the psutil package.

Install using pip:
    $ pip install psutil
    
Install using conda:
    $ conda install psutil


In [35]:
zs = ode_scipy(predict_fn, z0, ts, args)

xs = zs[:, 0].numpy()
ys = zs[:, 1].numpy()

iplot([go.Scatter(x=ts.numpy(), y=xs, name="x"), go.Scatter(x=ts.numpy(), y=ys, name="y")])

iplot([go.Scatter(x=xs, y=ys)])

In [36]:
from tensorflow.keras import initializers

D = 2
N = 1000
batch_time = 10
batch_size = 20
ts = tf.constant(np.linspace(0., 25.0, N))
z0 = tf.Variable(tf.constant([2.0, 0.0], shape=(2,), dtype=ts.dtype))

args = tf.Variable(tf.constant([
    # −0.1x^3 + 2.0y^3
    [-0.1, 2.0],
    # −2.0x^3 − 0.1y^3
    [-2.0, -0.1]], shape=(2, 2), dtype=ts.dtype))


model2 = tf.keras.Sequential([
  tf.keras.layers.Dense(25, activation=tf.nn.tanh, input_shape=(1, D),
                        kernel_initializer=initializers.RandomNormal(mean=0.0, stddev=0.1)),
  tf.keras.layers.Dense(D)
])

def predict_fn2(y, ts, args):
    rank =  tf.rank(y).numpy()
    if rank == 1:
        y = tf.expand_dims(y, 0)
    y = tf.cast(y, tf.float32)
    y = tf.math.pow(y, 3)
    r = model2(y)
    if rank == 1:
        r = tf.squeeze(r)
    r = tf.cast(r, y.dtype)
    return r

ground_truth2 = ode_scipy(damped_oscillator_2d, z0, ts, args)

#func = lambda z0, ts, args: tf.tensordot(z0**3, args, axes=1)
#ground_truth2 = ode_tf(func, z0, ts, args)

In [37]:
optimize_batch(predict_fn2, ode_scipy_batch_solver,
         loss_L1, ground_truth2, z0, ts,
         learning_rate=0.001,
         batch_time=batch_time, data_size=N, batch_size=batch_size, test_freq=1,
         args=None, variables=model2.variables, epochs=500,
         x_axis_min=-0.25, x_axis_max=6.25,
         y_axis_min=-2.5, y_axis_max=2.5,
         x2_axis_min=-2.5, x2_axis_max=2.5,
         y2_axis_min=-2.5, y2_axis_max=2.5,
         output_dir="ode_dense_damped_oscillator_2d_2", start=0)

ValueError: Image generation requires the psutil package.

Install using pip:
    $ pip install psutil
    
Install using conda:
    $ conda install psutil


In [ ]:
! pip install matplotlib

https://github.com/ZainRaza14/Neural-ODE/blob/master/ODE.ipynb

In [44]:
import numpy as np
from scipy.integrate import odeint
import matplotlib.pyplot as plt

In [45]:
import torch
import torch.nn as nn

In [46]:
class Flatten(nn.Module):

    def __init__(self):
        super(Flatten, self).__init__()

    def forward(self, x):
        shape = torch.prod(torch.tensor(x.shape[1:])).item()
        return x.view(-1, shape)

def conv1x1(in_planes, out_planes, stride=1):
    """1x1 convolution"""
    return nn.Conv2d(in_planes, out_planes, kernel_size=1, stride=stride, bias=False)

def norm(dim):
    return nn.GroupNorm(min(32, dim), dim)

def conv3x3(in_planes, out_planes, stride=1):
    """3x3 convolution with padding"""
    return nn.Conv2d(in_planes, out_planes, kernel_size=3, stride=stride, padding=1, bias=False)

## Import the Adjoint Method (ODE Solver)
from torchdiffeq import odeint_adjoint as odeint

## Normal Residual Block Example

class ResBlock(nn.Module):

    #init a block - Convolve, pool, activate, repeat
    def __init__(self, inplanes, planes, stride=1, downsample=None):
        super(ResBlock, self).__init__()
        self.norm1 = norm(inplanes)
        self.relu = nn.ReLU(inplace=True)
        self.downsample = downsample
        self.conv1 = conv3x3(inplanes, planes, stride)
        self.norm2 = norm(planes)
        self.conv2 = conv3x3(planes, planes)

    #Forward pass - pass output of one layer to the input of the next 
    def forward(self, x):
        shortcut = x
        out = self.relu(self.norm1(x))
        out = self.conv1(out)
        out = self.norm2(out)
        out = self.relu(out)
        out = self.conv2(out)

        return out + shortcut

## Ordinary Differential Equation Definition

In [48]:
class ODEfunc(nn.Module):

    # init ODE variables
    def __init__(self, dim):
        super(ODEfunc, self).__init__()
        self.norm1 = norm(dim)
        self.relu = nn.ReLU(inplace=True)
        self.conv1 = conv3x3(dim, dim)
        self.norm2 = norm(dim)
        self.conv2 = conv3x3(dim, dim)
        self.norm3 = norm(dim)
        self.nfe = 0

    # init ODE operations 
    def forward(self, t, x):
      #nfe = number of function evaluations per timestep
        self.nfe += 1
        out = self.norm1(x)
        out = self.relu(out)
        out = self.conv1(out)
        out = self.norm2(out)
        out = self.relu(out)
        out = self.conv2(out)
        out = self.norm3(out)
        return out
    
## ODE block
class ODEBlock(nn.Module):

    #initialized as an ODE Function
    #count the time
    def __init__(self, odefunc):
        super(ODEBlock, self).__init__()
        self.odefunc = odefunc
        self.integration_time = torch.tensor([0, 1]).float()

    #foorward pass 
    #input the ODE function and input data into the ODE Solver (adjoint method)
    # to compute a forward pass
    def forward(self, x):
        self.integration_time = self.integration_time.type_as(x)
        out = odeint(self.odefunc, x, self.integration_time, rtol=args.tol, atol=args.tol)
        return out[1]

    @property
    def nfe(self):
        return self.odefunc.nfe

    @nfe.setter
    def nfe(self, value):
        self.odefunc.nfe = value

In [50]:
device = torch.device('cuda:' + str(args.gpu) if torch.cuda.is_available() else 'cpu')

In [54]:
## Main Method

if __name__ == '__main__':


    
    #Add Pooling
    downsampling_layers = [
         nn.Conv2d(1, 64, 3, 1),
         ResBlock(64, 64, stride=2, downsample=conv1x1(64, 64, 2)),
         ResBlock(64, 64, stride=2, downsample=conv1x1(64, 64, 2)),
     ]

    # Initialize the network as 1 ODE Block
    feature_layers = [ODEBlock(ODEfunc(64))] 
    # Fully connected Layer at the end
    fc_layers = [norm(64), nn.ReLU(inplace=True), nn.AdaptiveAvgPool2d((1, 1)), Flatten(), nn.Linear(64, 10)]
  
    #The Model consists of an ODE Block, pooling, and a fully connected block at the end
    model = nn.Sequential(*downsampling_layers, *feature_layers, *fc_layers).to(device)

    #Declare Gradient Descent Optimizer
    optimizer = torch.optim.SGD(model.parameters(), lr=0.001, momentum=0.9)
    
    nepochs=10
    batches_per_epoch=10
    #Training Loop
    for itr in range(nepochs * batches_per_epoch):

        
        #init the optimizer
        optimizer.zero_grad()
        
        #Generate training data
        x, y = data_gen()
        #Input Training data to model, get Prediction
        logits = model(x)
        #Compute Error using Prediction vs Actual Label
        loss = CrossEntropyLoss(logits, y)
        
        #Backpropagate
        loss.backward()
        optimizer.step()

NameError: name 'data_gen' is not defined